# Setup

### Previous Script

In [1]:
%run ./1_Master_Script.ipynb

# Overwrite the studyarea parameter
parameter_studyarea = 'Continent'

%run ./2_Cleaning_Layers.ipynb
%run ./3.1_City_Scraping.ipynb
%run ./3.2_City_Cleaning.ipynb

Master Script has been run successfully!
Cleaning Layers Script has been run successfully!
Chosen Study Area: Continent
Days since last generation: 0
Regenerate Cities: False
City Scraping Script has been run successfully!
RESULT: From 851 cities, 158 were removed, leaving just 693.
RESULT: From 693 cities, 2 were removed, leaving just 691.
City Cleaning Script has been run successfully!


# Cleaning

### Add Cities

Cities data was cleaned in a prior script, but isn't yet part of the dict.

In [2]:
city_dict = final_dict.copy()

city_dict['cities'] = final_cities.copy()

### Borders

#### Country Filter & Group River Kingdoms

For this QGIS map, I want specific vector geometries.

In [3]:
borders_dict = city_dict.copy()

# COUNTRY FILTER

country_list = [
    'Brevoy',
    'Narland', # This is Stolen Lands
    'River Kingdoms',
    'Numeria',
    'Mendev',
    'Ustalav',
    'Sarkoris Scar',
    'Realm of Mammoth Lords'
]

con1 = borders_dict['borders']['nation'].isin(country_list)
con2 = borders_dict['borders']['subregion'] == 'River Kingdoms'

borders_dict['borders'] = borders_dict['borders'].loc[(con1 == True) | (con2 == True)]

# GROUP RIVER KINGDOMS

# Group it, but remove The Stolen Lands
river_kingdoms = borders_dict['borders'].loc[(con2 == True)].copy()
river_kingdoms = river_kingdoms.loc[river_kingdoms['province'] != 'Narland']
river_kingdoms_united = river_kingdoms.dissolve().copy()
river_kingdoms_united['nation'] = 'River Kingdoms'
river_kingdoms_united['province'] = np.nan
river_kingdoms_united['subregion'] = np.nan

# Create a separate Narland, NOT including Pitax
stolen_lands = borders_dict['borders'].loc[borders_dict['borders']['province'] == 'Narland'].copy()
stolen_lands['nation'] = 'Stolen Lands'
stolen_lands['province'] = np.nan
stolen_lands['subregion'] = np.nan

# Remove the split kingdoms
borders_dict['borders'] = borders_dict['borders'].loc[(con2 == False)]

# Add in the united River Kingdoms
borders_dict['borders'] = pd.concat([borders_dict['borders'],river_kingdoms_united])

# Add in The Stolen Lands
borders_dict['borders'] = pd.concat([borders_dict['borders'],stolen_lands])

# Diagnostic
m = final_dict['borders'].explore(color = 'blue')
m = borders_dict['borders'].explore(m=m, color = 'red')
#m = stolen_lands.explore(m=m, color = 'yellow')

m

#### Terrain Filter

I'm interested only in terrain within some units of the borders. This will cut down on computational waste in QGIS.

In [4]:
buffer_dict = borders_dict.copy()

borders_geo = buffer_dict['borders'].dissolve()

borders_buffer = borders_geo.copy()
borders_buffer['geometry'] = borders_buffer.buffer(1000000) # meters

# Clip

for item in buffer_dict:

    buffer_dict[item] = gpd.clip(buffer_dict[item], borders_buffer)

# Buffer Diagnostic
m = borders_geo.explore(color = 'blue')
m = borders_buffer.explore(m=m, color = 'red')
m = final_dict['borders'].explore(m=m, color = 'white')

m

In [5]:
# Clip Diagnostic

m = borders_dict['waters'].explore(color = 'blue')
m = buffer_dict['waters'].explore(m=m, color = 'red')
m = final_dict['waters'].explore(m=m, color = 'white')

m

### Dissolve-Explode Water

Water bodies are sometimes split into multiple geometries despite being contiguous. This helps in some contexts, but not mine. On QGIS, this means coloring the boundaries will create confusing outlines, wherein you see straight lines cutting up water bodies. By Dissolve-exploding them, those lines disappear. Without using some more nuanced method, however, this means losing data like the name of a given water body, but this is not a major downside.

In [6]:
waters_dict = buffer_dict.copy()

waters_modified = waters_dict['waters'].copy()

waters_modified = waters_modified.dissolve()

waters_modified = waters_modified.explode()

waters_dict['waters'] = waters_modified.copy()

# Diagnostic
m = waters_dict['waters'].explore(color = 'red')

m

### Special Cities

On the map, I want to show only specific cities, of varying qualifications.

In [7]:
special_dict = waters_dict.copy()

#### Key Cities

Here we identify, in a separate object, the city cities we want to highlight.

In [8]:
# Restov, Ustalav, that's it

key_cities_list = ['Caliphas','Restov']

key_cities = special_dict['cities'].loc[special_dict['cities']['Name'].isin(key_cities_list)].reset_index(drop = True).copy()

key_cities

Name                                             link  capital  size  \
0    Restov           https://pathfinderwiki.com/wiki/Restov    False     1   
1  Caliphas  https://pathfinderwiki.com/wiki/Caliphas_(city)     True     1   

                                                text  articleLength  \
0  <p><b>Restov</b> is one of the two largest cit...           2300   
1  <p>A city made rich by trade from across <a hr...           3700   

                           geometry   Capital               Titles Leader  \
0    POINT (158644.337 1950591.798)      <NA>  Free City of Restov   <NA>   
1  POINT (-1403458.993 1890113.413)  Caliphas   County of Caliphas   <NA>   

   ...                        Ruler  Land        Size  \
0  ...  Lord Mayor Ioseph Sellemius  <NA>  Large city   
1  ...   Prince Aduard Ordranti III  <NA>        <NA>   

                                        Demographics Level Demonym  \
0  15,240 humans, 1,220 dwarves, 950 gnomes, 820 ...     9    <NA>   
1                                               <NA>  <NA>    <NA>   

         Government Population Scope  size0  
0         Autocracy      18670  <NA>  False  
1  Autocratic noble       <NA>  <NA>  False  

[2 rows x 31 columns]

#### Big Cities

Let's create a separate layer for max size cities.

In [9]:
big_cities = special_dict['cities'].loc[special_dict['cities']['size0'] == True].reset_index(drop = True).copy()

#### Internal Cities

These are cities within the borders of the countries of interest.

In [10]:
internal_cities = gpd.clip(special_dict['cities'],special_dict['borders'])

### Final Mapping

In [11]:
map_dict = special_dict.copy()

# Diagnostic

### Add Cities

The old layer doesn't have the old cities. Gotta add first.

In [12]:
crs_dict['cities'] = crs_cities

### Visual

#### General

In [13]:
explored_layer = 'waters'
examined_step = map_dict.copy()

ax = studyarea.explore(color = 'cyan')

# Important to compare to crs_dict, NOT layers_dict! THIS IS BECAUSE OF DIFFERENT CRS
ax = crs_dict[explored_layer][['Name','geometry']].explore(m=ax, color = 'red')
ax = examined_step[explored_layer][['Name','geometry']].explore(m=ax, color = 'yellow')

#ax

#### Cities

In [15]:
explored_layer = 'cities'
examined_step = map_dict.copy()

ax = studyarea.explore(color = 'cyan')
ax = crs_dict['borders'].explore(m=ax, color = 'brown')
# Important to compare to crs_dict, NOT layers_dict! THIS IS BECAUSE OF DIFFERENT CRS
ax = crs_dict[explored_layer][['Name','capital','size','geometry']].explore(m=ax, color = 'red')
ax = examined_step[explored_layer][['Name','capital','size','geometry']].explore(m=ax, color = 'yellow')
# Capitals
capital = crs_dict[explored_layer][['Name','capital','size','geometry']].copy()
capital = capital.loc[capital['capital'] == True]
ax = capital.explore(m=ax, color = 'white')

ax

# Export

Later, check out automatically creating the map in QGIS. For now, just export to QGIS and work there.

In [18]:
export_dict = map_dict.copy()

# Dictionary Layers
path = clean_loc + 'QGIS_Layers/'

for item in export_dict:

    export_dict[item].to_file(path + item + '.geojson')

# External Layers

for item in final_dict:

    final_dict[item].to_file(path + item + '_external' + '.geojson')

# Region Layers
river_kingdoms.to_file(path + 'river_kingdoms' + '.geojson')
stolen_lands.to_file(path + 'stolen_lands' + '.geojson')

# Capital Cities
capital.to_file(path + 'capital.geojson')

# Key Cities
key_cities.to_file(path + 'cities_key.geojson')

# Big Cities
big_cities.to_file(path + 'cities_big.geojson')

# Internal Cities

internal_cities.to_file(path + 'cities_internal.geojson')

# Run Message

This is to show key info when this script is run in another script.

In [ ]:
print("Kingmaker Intro Map Script has been run successfully!")